# Analysis of flight delays for Newark Airport

Project Brief: See project documentation for full description.

Newark airport has requested an investigation into flight departure delays.<br /> 
Flight delays are a key performance indicator of airport operations. <br /> 
The following three business questions are explored:<br /> 

- What is the impact of weather on flight departure delays
- What other reasons impact flight departure delays
- How does Newark compare to other NY airports

In [3]:
# import libraries
import pandas as pd
import numpy as np
import pandas_profiling as pp
import datetime as dt
import seaborn as sns
from matplotlib import pyplot as plt
import folium

In [10]:
# read in data
flights_all = pd.read_csv('../data/clean_data/flights_data.csv', index_col=0)

#create Newark only dataset
ewr_flights = flights_all.loc[(flights_all['origin'] == 'EWR')].copy().reset_index(drop=True)

# Exploratory data analysis

## Investigating weather data

In [13]:
# profile report for weather variables
pp.ProfileReport(ewr_flights.loc[:, ['time_hour', 'dep_delay_true', 'wind_dir',
       'wind_speed', 'wind_gust', 'visib', 'temp_max', 'temp_min',
       'temp_ave', 'temp_departure', 'ppt', 'new_snow', 'snow_depth']])

Render HTML: 100%|██████████| 1/1 [00:02<00:00,  2.37s/it]


Investigating the weather variables, `wind_speed` and `wind_gust` are highly positively correlated. As are all the temperature variables, `temp_max`, `temp_min`, `temp_ave`. <br />
Precipitation (`ppt`) has a very skewed distribution and 48% of the data is zero. The two snow variables, `new_snow` and `snow_depth` have 92% zeros in their data columns. <br />
Wind direction has a bimodal distribution. <br />
24% of the flights are delayed and 76% of the flights are not delayed.

## Investigating plane information

In [15]:
pp.ProfileReport(flights_all.loc[:,['manufacturer', 'type', 'carrier_name', 'engine', 'model']])

Render HTML: 100%|██████████| 1/1 [00:00<00:00,  5.97it/s]



- The `type` variable is highly correlated with `manufacturer` and `engine`, remove this variable. <br />
- The `manufacturer` variable has high cardinality (lots of different categories). Recode this to the top 5 manufacturers, recode NaNs to unknown and set the rest to other.

# Preparing data for modelling

## Variable engineering

 - convert `wind_speed` into a categorical `wind_scale` using the Beaufort scale
 - drop columns with high correlation identified in pandas profiling report (`wind_gust`, `temp_max`, `temp_min`)
 - remove this `type`
 - recode `manufacturer` to the top 5 manufacturers, recode NaNs to unknown and set the rest to other

In [ ]:
# add categorical wind_scale for wind_speed
wind_labels = ['Calm', 'Light Breeze', 'Gentle Breeze', 
'Moderate Breeze', 'Fresh Breeze', 'Strong Breeze', 'Near Gale',
'Gale']

wind_bins = [0, 3, 7, 12, 18, 24, 31, 38, 46]

flights_all['wind_scale'] = pd.cut(flights_all['wind_speed'], 
bins = wind_bins, labels=wind_labels,
include_lowest = True)

In [ ]:
weather_drop = ['wind_gust', 'temp_max', 'temp_min']

flights_all_trim = flights_all.drop(columns=weather_drop)

In [ ]:
flights_all_trim.drop(columns=['type', 'model'], inplace = True)

man_keep = ['Unknown', 'BOEING', 'AIRBUS', 'AIRBUS INDUSTRIE',
 'EMBRAER', 'BOMBARDIER INC', 'MCDONNELL DOUGLAS AIRCRAFT CO', 'MCDONNELL DOUGLAS']

flights_all_trim.manufacturer = np.where(flights_all_trim.manufacturer.isin(man_keep),
flights_all_trim.manufacturer, 'Other')

flights_all_trim.head()

In [ ]:
#fix manufacturer doubling for airbus and mcdonnell douglas
flights_all_trim.manufacturer = flights_all_trim.manufacturer.map({
    'AIRBUS INDUSTRIE': 'AIRBUS',
    'AIRBUS': 'AIRBUS',
    'MCDONNELL DOUGLAS': 'MCDONNELL DOUGLAS',
    'MCDONNELL DOUGLAS AIRCRAFT CO': 'MCDONNELL DOUGLAS',
    'BOEING': 'BOEING',
    'EMBRAER': 'EMBRAER', 
    'BOMBARDIER INC': 'BOMBARDIER INC',
    'Unknown': 'Unknown',
    'Other': 'Other'})

flights_all_trim.head()

In [ ]:
flights_all_trim.shape

Remove other columns not thought to be important for flight delay model:

NB - leave dest_airport!

Remove:
dest_timezone, dest_alt, dest_lon, dest_lat, dest_faa, ori_timezone, ori_lat, ori_lon, ori_airport, ori_faa, time_hour, minute, hour, dest, tailnum, flight, carrier, arr_delay, sched_arr_time, arr_time, dep_delay, sched_dep_time, dep_time, day.

Leave hour but convert to categorical add am or pm?

Add season column?